### Importing libraries

In [129]:
import pandas as pd  # Dataframes
import numpy as np  # missing data and efficient arrays
import folium  # Maps
from geopy.geocoders import Nominatim  # Address --> lat & long
from time import sleep  # Add in delays, which helps with API calls
import requests  # Get information from URLs

### Sourcing data

Borough profiles - https://data.london.gov.uk/dataset/london-borough-profiles

In [130]:
# Profiles of the London Boroughs

borough_df = pd.read_excel("london-borough-profiles.xlsx", sheet_name="Data")

borough_df.head()

Code   New code             Area name Inner/ Outer London  \
0        NaN        NaN                   NaN                 NaN   
1  E09000001  E09000001        City of London        Inner London   
2  E09000002  E09000002  Barking and Dagenham        Outer London   
3  E09000003  E09000003                Barnet        Outer London   
4  E09000004  E09000004                Bexley        Outer London   

   GLA Population Estimate 2017 GLA Household Estimate 2017  \
0                           NaN                         NaN   
1                        8800.0                     5325.82   
2                      209000.0                     78188.4   
3                      389600.0                      151423   
4                      244300.0                     97735.8   

  Inland Area (Hectares) Population density (per hectare) 2017  \
0                    NaN                                   NaN   
1                290.393                               30.3037   
2                3610.78                               57.8822   
3                8674.83                               44.9115   
4                6058.07                               40.3264   

   Average Age, 2017  Proportion of population aged 0-15, 2015  ...  \
0                NaN                                       NaN  ...   
1               43.2                                      11.4  ...   
2               32.9                                      27.2  ...   
3               37.3                                      21.1  ...   
4               39.0                                      20.6  ...   

   Happiness score 2011-14 (out of 10)  Anxiety score 2011-14 (out of 10)  \
0                                  NaN                                NaN   
1                                 5.99                               5.57   
2                                 7.05                               3.05   
3                                 7.37                               2.75   
4                                 7.21                               3.29   

  Childhood Obesity Prevalance (%) 2015/16 People aged 17+ with diabetes (%)  \
0                                                                        NaN   
1                                      NaN                          2.637945   
2                                   28.542                          7.272108   
3                                  20.6579                          6.026084   
4                                  22.7093                          6.859383   

  Mortality rate from causes considered preventable 2012/14  \
0                                                NaN          
1                                            128.833          
2                                            227.605          
3                                             133.77          
4                                            164.286          

  Political control in council  \
0                          NaN   
1                            .   
2                          Lab   
3                         Cons   
4                         Cons   

  Proportion of seats won by Conservatives in 2014 election  \
0                                                NaN          
1                                                  .          
2                                                  0          
3                                            50.7937          
4                                            71.4286          

  Proportion of seats won by Labour in 2014 election  \
0                                                NaN   
1                                                  .   
2                                                100   
3                                                  .   
4                                            23.8095   

  Proportion of seats won by Lib Dems in 2014 election  \
0                                                NaN     
1                             

In [131]:
# Details of average income in 2017 (multi-index)

income_df = pd.read_excel("https://data.london.gov.uk/download/average-income-tax-payers-borough/392e86d4-f1d3-4f06-a6a5-7fcd0fd65948/income-of-tax-payers.xls",
                          sheet_name=1, header=[0,1])

income_df.head()

Unnamed: 0_level_0    Unnamed: 1_level_0               1999-00            \
                Code                  Area Number of Individuals    Mean £   
0          E09000001        City of London               10000.0  109800.0   
1          E09000002  Barking and Dagenham               62000.0   16200.0   
2          E09000003                Barnet              161000.0   26800.0   
3          E09000004                Bexley              105000.0   20500.0   
4          E09000005                 Brent              122000.0   20000.0   

                         2000-01                                  2001-02  \
  Median £ Number of Individuals    Mean £ Median £ Number of Individuals   
0  40400.0               10000.0  137000.0  65000.0               12000.0   
1  15100.0               71000.0   18100.0  15600.0               56000.0   
2  18700.0              156000.0   30800.0  19400.0              159000.0   
3  17200.0              116000.0   19800.0  17300.0              112000.0   
4  16500.0              130000.0   22200.0  16800.0              127000.0   

            ...  2013-14               2014-15                     \
    Mean £  ... Median £ Number of Individuals    Mean £ Median £   
0  92900.0  ...  65300.0                9000.0  144000.0  61100.0   
1  18600.0  ...  21000.0               74000.0   25500.0  21800.0   
2  30400.0  ...  26800.0              175000.0   45800.0  27100.0   
3  22000.0  ...  24400.0              122000.0   30200.0  24400.0   
4  21100.0  ...  21300.0              147000.0   31200.0  22700.0   

                2015-16                                  2016-17            \
  Number of Individuals    Mean £ Median £ Number of Individuals    Mean £   
0               10000.0  142000.0  60000.0               12000.0  157000.0   
1               83000.0   25900.0  22100.0               88000.0   26700.0   
2              178000.0   49000.0  27700.0              180000.0   48600.0   
3              127000.0   30900.0  24500.0              125000.0   32300.0   
4              154000.0   32600.0  23200.0              155000.0   34100.0   

            
  Median £  
0  57300.0  
1  23300.0  
2  28800.0  
3  26100.0  
4  24100.0  

[5 rows x 53 columns]

### Preparing data 

The first step is to clean up the borough dataframe

In [132]:
# Drop empty or aggregate rows in borough df

borough_df = borough_df[1:34]

In [135]:
# Subset the borough dataframe, removing unneeded columns

borough_df = borough_df[['Area name',
                         'GLA Population Estimate 2017',
                         'Population density (per hectare) 2017',
                         'Average Age, 2017',
                         'Employment rate (%) (2015)',
                         'Median House Price, 2015',
                         '% of area that is Greenspace, 2005',
                         'Average Public Transport Accessibility score, 2014',
                         'Life satisfaction score 2011-14 (out of 10)',
                         'Happiness score 2011-14 (out of 10)']]

In [136]:
# Rename the columns to be more meaningful

borough_df.columns = ['borough',
                     'population',
                     'population_density',
                     'average_age',
                     'percentage_employment',
                     'median_house_price',
                     'percentage_greenspace',
                     'public_transport_accessibility_score',
                     'life_satisfaction_score',
                     'happiness_score']

In [137]:
# View the dataframe

borough_df.head()

borough  population population_density  average_age  \
1        City of London      8800.0            30.3037         43.2   
2  Barking and Dagenham    209000.0            57.8822         32.9   
3                Barnet    389600.0            44.9115         37.3   
4                Bexley    244300.0            40.3264         39.0   
5                 Brent    332100.0             76.817         35.6   

   percentage_employment median_house_price percentage_greenspace  \
1                   64.6             799999                   4.8   
2                   65.8             243500                  33.6   
3                   68.5             445000                  41.3   
4                   75.1             275000                  31.7   
5                   69.5             407250                  21.9   

  public_transport_accessibility_score  life_satisfaction_score  \
1                               7.8623                     6.59   
2                              2.97063                     7.14   
3                               2.9967                     7.48   
4                              2.55213                     7.38   
5                              3.65371                     7.25   

   happiness_score  
1             5.99  
2             7.05  
3             7.37  
4             7.21  
5             7.22

Once the borough dataframe contains only the desired data, with meaningful headers, we can focus on the income dataframe.

In [138]:
# Collapse the multi-index

income_df.columns = [' '.join(col).strip() for col in income_df.columns.values]

# Keep only required columns

income_df = income_df[["Unnamed: 1_level_0 Area", "2016-17 Mean £"]]

# Rename the columns meaningfully

income_df.columns = ["borough", "mean_income"]

Next, we merge `income_df` into the borough dataframe.

In [139]:
# Replace "-" with spaces in income_df, so that it matches borough_df

income_df.replace("-", " ", regex=True, inplace=True)

# Merge the dataframes

borough_df = borough_df.merge(income_df, on="borough")

# view the dataframe

borough_df.head()

borough  population population_density  average_age  \
0        City of London      8800.0            30.3037         43.2   
1  Barking and Dagenham    209000.0            57.8822         32.9   
2                Barnet    389600.0            44.9115         37.3   
3                Bexley    244300.0            40.3264         39.0   
4                 Brent    332100.0             76.817         35.6   

   percentage_employment median_house_price percentage_greenspace  \
0                   64.6             799999                   4.8   
1                   65.8             243500                  33.6   
2                   68.5             445000                  41.3   
3                   75.1             275000                  31.7   
4                   69.5             407250                  21.9   

  public_transport_accessibility_score  life_satisfaction_score  \
0                               7.8623                     6.59   
1                              2.97063                     7.14   
2                               2.9967                     7.48   
3                              2.55213                     7.38   
4                              3.65371                     7.25   

   happiness_score  mean_income  
0             5.99     157000.0  
1             7.05      26700.0  
2             7.37      48600.0  
3             7.21      32300.0  
4             7.22      34100.0

In [140]:
# Create a geolocator object

geolocator = Nominatim(user_agent="explorer")

# Function to get the location of a London borough

def get_london_location(name):
    sleep(0.3)
    loc = geolocator.geocode(f"Borough of {name}, London, UK")
    if loc == None:
        sleep(0.3)
        loc = geolocator.geocode(f"{name}, London, UK")
    return loc.latitude, loc.longitude

# Extract the lat and long for each location

locations = borough_df["borough"].apply(lambda name: get_london_location(name))

In [141]:
# Add the latitude and longitude to borough_df as columns

borough_df["latitude"], borough_df["longitude"] = list(zip(*locations))

In [142]:
# Fix the lat/long for Havering, which has to be named "borough of" in order t ofind the right location.
location = geolocator.geocode("City of London, London, UK")
borough_df.loc[borough_df["borough"] == "City of London", "latitude"] = location.latitude
borough_df.loc[borough_df["borough"] == "City of London", "longitude"] = location.longitude

In [143]:
# View the dataframe

borough_df.head()

borough  population population_density  average_age  \
0        City of London      8800.0            30.3037         43.2   
1  Barking and Dagenham    209000.0            57.8822         32.9   
2                Barnet    389600.0            44.9115         37.3   
3                Bexley    244300.0            40.3264         39.0   
4                 Brent    332100.0             76.817         35.6   

   percentage_employment median_house_price percentage_greenspace  \
0                   64.6             799999                   4.8   
1                   65.8             243500                  33.6   
2                   68.5             445000                  41.3   
3                   75.1             275000                  31.7   
4                   69.5             407250                  21.9   

  public_transport_accessibility_score  life_satisfaction_score  \
0                               7.8623                     6.59   
1                              2.97063                     7.14   
2                               2.9967                     7.48   
3                              2.55213                     7.38   
4                              3.65371                     7.25   

   happiness_score  mean_income   latitude  longitude  
0             5.99     157000.0  51.515618  -0.091998  
1             7.05      26700.0  51.554117   0.150504  
2             7.37      48600.0  51.612523  -0.211444  
3             7.21      32300.0  51.461969   0.145699  
4             7.22      34100.0  51.563826  -0.275760

With the borough dataframe complete, we can now plot borough information on a map. To do that, we need a geoJSON file.

In [144]:
# Store the name of the geoJSON file

borough_geo = r"london_boroughs.geojson"

### Exploring Data

In [128]:
london_map = folium.Map(location=[51.509865, -0.118092], zoom_start=10)

choropleth = folium.Choropleth(geo_data = borough_geo,
                               data = borough_df,
                               columns = ['Area name', 'mean_income'],
                               key_on = 'feature.properties.name',
                               fill_color = 'YlOrRd', 
                               fill_opacity = 0.5, 
                               line_opacity = 0.4,
                               legend_name = 'Average income',
                               name="Income",
                               show=False)

choroplet2 = folium.Choropleth(geo_data = borough_geo,
                               data = borough_df,
                               columns = ['Area name', 'Average Age, 2017'],
                               key_on = 'feature.properties.name',
                               fill_color = 'YlOrRd', 
                               fill_opacity = 0.5, 
                               line_opacity = 0.4,
                               legend_name = 'Average age',
                               name="Age",
                               show=False)

# Add the choropleths to the map

choropleth.add_to(london_map)
choroplet2.add_to(london_map)

borough_markers = folium.FeatureGroup(name="Borough markers").add_to(london_map)

for lat, lng, borough in zip(borough_df['latitude'], borough_df['longitude'], borough_df['Area name']):
    pop = folium.Popup(f"{borough}", parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=3,
        popup=pop,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(borough_markers)

# Add layer controls to the map

folium.LayerControl().add_to(london_map)


london_map

In [112]:
# Create 4square credentials

CLIENT_ID = '4GLLROGJFFVYQ5CALGAYFYBLAN5Y50SROVY4ULAKVBPJSYXJ' # your Foursquare ID
CLIENT_SECRET = 'N2GZM4QEABD4IFWWT0WGPUE2DL45NAX5VU5ED0PXMGB4T4SM' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 500

In [123]:
# Function to extract venues for each borough

def getNearbyVenues(names, latitudes, longitudes, radius=5000):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Borough', 
                  'Borough Latitude', 
                  'Borough Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [124]:
# Get venues for all postcodes

venues = getNearbyVenues(names=borough_df['Area name'],
                         latitudes=borough_df['latitude'],
                         longitudes=borough_df['longitude'])

In [116]:
venue_df = venues

In [125]:
venue_df

Borough  Borough Latitude  Borough Longitude  \
0    City of London         51.515618          -0.091998   
1    City of London         51.515618          -0.091998   
2    City of London         51.515618          -0.091998   
3    City of London         51.515618          -0.091998   
4    City of London         51.515618          -0.091998   
..              ...               ...                ...   
814     Westminster         51.514426          -0.160866   
815     Westminster         51.514426          -0.160866   
816     Westminster         51.514426          -0.160866   
817     Westminster         51.514426          -0.160866   
818     Westminster         51.514426          -0.160866   

                              Venue  Venue Latitude  Venue Longitude  \
0    Goodman Steak House Restaurant       51.514398        -0.090745   
1               Hawksmoor Guildhall       51.515647        -0.090997   
2                       Daunt Books       51.513982        -0.092995   
3                        City Càphê       51.514750        -0.091545   
4                     The Ned Hotel       51.513755        -0.090067   
..                              ...             ...              ...   
814            مطعم المسكوف العراقي       51.515061        -0.165589   
815      The Victoria Casino London       51.517025        -0.165797   
816                          Clarks       51.513764        -0.154878   
817           Victory Services Club       51.514144        -0.162314   
818                    River Island       51.513834        -0.154884   

            Venue Category  
0               Steakhouse  
1               Steakhouse  
2                Bookstore  
3    Vietnamese Restaurant  
4                    Hotel  
..                     ...  
814             Restaurant  
815                 Casino  
816             Shoe Store  
817                  Hotel  
818         Clothing Store  

[819 rows x 7 columns]

In [121]:
london_map